In [1]:
import pandas as pd
import spacy

from gensim.models import LdaModel

import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from gensim.models import CoherenceModel

import nltk
import re
from gensim.models import Phrases
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
nltk.download('wordnet')
from gensim.corpora import Dictionary
nltk.download('omw-1.4')

import pyLDAvis.gensim_models
import warnings

from nltk.corpus import stopwords
from nltk import word_tokenize
from nltk.tokenize import sent_tokenize
import re


#from snowballstemmer import stemmer

C:\Users\tlp\Anaconda3\lib\site-packages\pandas\core\computation\expressions.py:20: UserWarning: Pandas requires version '2.7.3' or newer of 'numexpr' (version '2.7.1' currently installed).
  from pandas.core.computation.check import NUMEXPR_INSTALLED
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\tlp\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\tlp\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


In [2]:
# ! pip install spacy

### Lecture des fichiers

In [2]:
df = pd.read_csv(r'C:\Users\tlp\Downloads\fullcorpus20210725_DATE.csv', encoding = 'ISO-8859-1').drop('Unnamed: 0',axis=1)
df.replace({
        '\xa0':'',
        '\x80':'',
        'Ã\x89':'É',
        'â\x99':' ',
        'Ã§':'ç',
        'Ã©': 'é', 
        'Ã¨': 'è', 
        'Ãª': 'ê', 
        'Ã´': 'ô',
        'Ã': 'à',
        'Â': '', 
        'â': "'", 
        'à ': 'à',
    }, regex=True, inplace = True)

print(df.shape)
df.head()

(8026, 9)


Journal  \
0   Le Figaro, no. 23520      
1               Le Monde      
2   Le Figaro (site web)      
3    Le Monde (site web)      
4    Le Monde (site web)      

                                               Titre        Date  \
0                 L'agenda caché de Moscou en Italie  2020-03-30   
1  Récit   Les trois semaines qui ont chamboulé l...  2020-03-27   
2  Élargissement de lâUnion européenne à lâheur...  2020-03-26   
3  Coronavirus: les trois semaines qui ont chambo...  2020-03-26   
4  Marc Lazar: «Plus lâItalie fait nation face à...  2020-03-25   

                                              Auteur  \
0                                 Lasserre, Isabelle   
1  Éric Albert, Cécile Boutelet, Jérôme Gautheret...   
2                                  Tandonnet, Maxime   
3  Eric Albert, Jérôme Gautheret, Cécile Boutelet...   
4                                         Marc Lazar   

                                               Texte  \
0  LES SYMBOLES comptent parfois plus que les fai...   
1  Londres, Berlin, Rome et Bruxelles corresponda...   
2  Fin observateur de la vie politique française ...   
3  Jeudi 26mars, les Vingt-Sept doivent se réunir...   
4  Tribune. LâItalie est le pays qui enregistre ...   

                                       extrait_debut  \
0   Sur les camions militaires qui, en colonnes, ...   
1   - Jeudi 26 mars, les Vingt-Sept devaient se r...   
2  contributeur régulier du FigaroVox, Maxime Tan...   
3  n visioconférence pour la troisième fois en mo...   
4   date du 25mars le plus grand nombre de morts ...   

                                         extrait_fin CJournal  \
0  Deux semaines pour se ressaisir et s'unir ou p...   Figaro   
1  pandémie touche tout le monde, indifféremment ...    Monde   
2  es yeux et de se préparer au changement dâun ...   Figaro   
3  e la tenue de ses comptes publics, nâest pas ...    Monde   
4  t de la School of Government de la Luiss (Libr...    Monde   

          crisis_term  
0  migrant_migratoire  
1  migrant_migratoire  
2  migrant_migratoire  
3  migrant_migratoire  
4  migrant_migratoire

### Préparation des données

In [30]:
# Testing
df = df.loc[df['Journal'].str.contains('Monde', regex=True)]#.head(100)
df.shape

(2077, 9)

In [5]:
# Import du package
import spacy

# pip install numpy=='1.22.1'
# pip install --upgrade h5py # ça m'a debloqué en redémarrant le kernel après ça

# Installation de la pipline entrainée pour la langue française
# !python -m spacy download fr_core_news_sm

In [6]:
nlp = spacy.load("fr_core_news_sm")

In [31]:
textes = df["Texte"]

In [32]:
%%time

spacy_docs = list(nlp.pipe(textes))

Wall time: 4min 29s


Prétraitement  
1) supprimer tous les mots de moins de 3 caractères,  # debatable  
2) supprimer tous les stop-words, et  
3) lemmatiser les mots restants et,  
4) mettre ces mots en minuscules.

In [33]:
%%time

docs = []
for doc in spacy_docs:
    tokens = []
    for token in doc:
        if len(token.orth_) > 3 and not token.is_stop: # prétraitements 1 et 2
            tokens.append( token.lemma_.lower() )  # TODO: prétraitements 3 et 4
    docs.append( tokens )

Wall time: 3.35 s


Afin de conserver un peu l'ordre des mots lors de notre modélisation, nous allons tenir en compte les bigrammes fréquents. Pour cela, nous allons utiliser la bibliothèque Gensim (excellente bibliothèque NLP pour les topics modeling et word embeddings)

Voici le processus retenu :

- Identifier les bigrammes fréquents dans le corpus,  
- Ajouter à la liste des tokens pour les documents dans lesquels ils apparaissent.  

Cela signifie que les bigrammes ne seront pas dans leur position correcte dans le texte, mais comme les topic models sont des modèles de bag-of-words (sac-de-mots en français) qui ignorent la position des mots, cela ne pose pas de problèmes

In [34]:
import re
from gensim.models import Phrases

bigram = Phrases(docs, min_count=10)

for index in range(len(docs)):
    for token in bigram[docs[index]]:
        if '_' in token:  # les bigrammes peuvent être reconnus par "_" qui concatène les mots
            docs[index].append(token) # TODO

In [35]:
from gensim.corpora import Dictionary

dictionary = Dictionary()

# Ajouter les documents un par un au dictionnaire
for doc in docs:
    dictionary.add_documents([doc])
    
print('Nombre de mots unique dans les documents initiaux :', len(dictionary))

# dictionary.filter_extremes(no_below=3, no_above=0.25)
# print('Nombre de mots unique dans les documents après avoir enlevé les mots fréquents/peu fréquents :', len(dictionary))

print("Exemple :", dictionary.doc2bow(docs[4]))

Nombre de mots unique dans les documents initiaux : 42806
Exemple : [(2, 2), (25, 1), (34, 1), (39, 1), (62, 1), (100, 1), (105, 1), (123, 2), (126, 1), (132, 2), (138, 3), (139, 4), (141, 1), (147, 1), (161, 1), (179, 1), (199, 2), (202, 1), (204, 1), (205, 6), (206, 4), (212, 1), (231, 1), (232, 1), (236, 2), (237, 1), (238, 1), (241, 12), (243, 1), (245, 1), (247, 1), (252, 1), (260, 1), (287, 1), (293, 1), (317, 1), (326, 1), (327, 1), (331, 1), (339, 1), (341, 1), (347, 1), (348, 1), (356, 4), (365, 2), (367, 2), (373, 1), (386, 1), (388, 1), (389, 1), (392, 4), (393, 1), (402, 8), (413, 6), (414, 1), (415, 1), (436, 1), (438, 1), (450, 1), (451, 1), (473, 2), (475, 2), (491, 3), (501, 1), (502, 2), (505, 1), (536, 1), (537, 1), (541, 1), (555, 1), (556, 2), (559, 4), (562, 1), (570, 1), (575, 3), (587, 1), (594, 1), (738, 2), (749, 2), (751, 1), (754, 1), (762, 1), (764, 1), (773, 1), (797, 1), (836, 3), (853, 2), (859, 1), (883, 1), (885, 2), (905, 1), (911, 1), (915, 1), (918, 

In [36]:
corpus = [ dictionary.doc2bow(doc) for doc in docs] # TODO

In [37]:
%%time
from gensim.models import LdaModel

model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=10, chunksize=1000, passes=5, random_state=1) # A REMPLIR

Wall time: 12.6 s


In [38]:
for (topic, words) in model.print_topics():
    print("***********")
    print("* topic", topic+1, "*")
    print("***********")
    print(topic+1, ":", words)
    print()

***********
* topic 1 *
***********
1 : 0.019*"parti" + 0.007*"droite" + 0.007*"élection" + 0.007*"extrême" + 0.007*"politique" + 0.006*"merkel" + 0.005*"conservateur" + 0.005*"italien" + 0.005*"démocrate" + 0.004*"gouvernement"

***********
* topic 2 *
***********
2 : 0.012*"gauche" + 0.009*"valls" + 0.009*"parti" + 0.008*"ministre" + 0.008*"politique" + 0.007*"candidat" + 0.007*"socialiste" + 0.007*"corbyn" + 0.007*"macron" + 0.007*"jeremy"

***********
* topic 3 *
***********
3 : 0.021*"réfugié" + 0.011*"migrant" + 0.011*"asile" + 0.010*"accueil" + 0.009*"allemagne" + 0.008*"accueillir" + 0.007*"france" + 0.007*"pays" + 0.006*"allemand" + 0.006*"demandeur"

***********
* topic 4 *
***********
4 : 0.012*"israà«l" + 0.009*"paris" + 0.006*"artiste" + 0.006*"israélien" + 0.005*"film" + 0.004*"femme" + 0.004*"cinéaste" + 0.003*"français" + 0.003*"réalisateur" + 0.003*"scène"

***********
* topic 5 *
***********
5 : 0.020*"européen" + 0.015*"pays" + 0.009*"europe" + 0.009*"réfugié" + 0.00

Visualisation

In [39]:
import pyLDAvis.gensim_models
import warnings

pyLDAvis.enable_notebook()
warnings.filterwarnings("ignore", category=DeprecationWarning) 

pyLDAvis.gensim_models.prepare(model, corpus, dictionary, sort_topics=False)

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.061227  0.113865       1        1   6.330902
1      0.088919  0.196137       2        1   2.390667
2     -0.132488 -0.098965       3        1   7.047414
3      0.186495 -0.135119       4        1   1.906715
4     -0.156977  0.004280       5        1  29.170046
5     -0.041137  0.122672       6        1   5.935852
6     -0.088470  0.048223       7        1   4.499892
7     -0.101191 -0.151167       8        1   9.567800
8     -0.058497 -0.021812       9        1  32.642748
9      0.242119 -0.078113      10        1   0.507964, topic_info=           Term         Freq        Total Category  logprob  loglift
1542    réfugié  5228.000000  5228.000000  Default  30.0000  30.0000
1231      parti  2316.000000  2316.000000  Default  29.0000  29.0000
413   politique  4779.000000  4779.000000  Default  28.0000  28.0000
979      social  1255.000000  1255.000000  Default  27.0000  27.0000
1482    migrant  3072.000000  3072.000000  Default  26.0000  26.0000
...         ...          ...          ...      ...      ...      ...
842   important    18.796604   641.560560  Topic10  -5.4997   1.7523
578        voir    19.045561  1148.933013  Topic10  -5.4865   1.1828
147     dernier    18.986539  1932.675133  Topic10  -5.4896   0.6596
356       monde    18.585011  2048.143903  Topic10  -5.5110   0.5802
888      moment    17.822043   684.739000  Topic10  -5.5529   1.6339

[840 rows x 6 columns], token_table=       Topic      Freq  Term
term                        
42487      4  0.951525  0,15
3733       1  0.028176  1983
3733       2  0.788918  1983
3733       9  0.169054  1983
3          1  0.295073  2017
...      ...       ...   ...
604        5  0.247848  être
604        6  0.029582  être
604        7  0.027183  être
604        8  0.136716  être
604        9  0.468513  être

[2618 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

Sur 10 articles

In [16]:
display(pyLDAvis.gensim_models.prepare(model, corpus, dictionary, sort_topics=False))
a=5

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.151830  0.052673       1        1  46.046441
1      0.077894 -0.055335       2        1   7.336751
2      0.001179  0.003691       3        1   0.019625
3     -0.005251 -0.011118       4        1   0.019625
4     -0.007771 -0.001691       5        1   0.019625
5     -0.009997  0.000822       6        1   0.019625
6      0.008660  0.048691       7        1  10.562539
7     -0.113458  0.144048       8        1  10.110144
8     -0.139928 -0.106716       9        1  12.844301
9      0.036842 -0.075065      10        1  13.021324, topic_info=           Term       Freq      Total Category  logprob  loglift
355        pays  37.000000  37.000000  Default  30.0000  30.0000
124       crise  31.000000  31.000000  Default  29.0000  29.0000
185    européen  42.000000  42.000000  Default  28.0000  28.0000
215   frontière  21.000000  21.000000  Default  27.0000  27.0000
184      europe  17.000000  17.000000  Default  26.0000  26.0000
..          ...        ...        ...      ...      ...      ...
185    européen   3.311762  42.060455  Topic10  -5.2978  -0.5030
452  solidarité   2.330292  10.394101  Topic10  -5.6493   0.5433
124       crise   2.978559  31.191356  Topic10  -5.4038  -0.3101
449   situation   2.272616  10.160216  Topic10  -5.6743   0.5410
519       virus   2.180482  11.872287  Topic10  -5.7157   0.3439

[652 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
949       1  0.964053          
1884      9  1.051185      1995
1478      2  0.941386      2006
1         1  0.862568      2012
2         1  0.390763      2015
...     ...       ...       ...
944       7  0.532964   émotion
2067      9  0.851912  émouvoir
1878      8  0.541189  éprouver
1672      8  0.293082      état
1672     10  0.586163      état

[670 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

In [40]:
# Nous en affichons que 4
n_doc = 4
i = 0
for (text, doc) in zip(textes[:n_doc], docs[:n_doc]):
    i += 1
    print("***********")
    print("* doc", i, "  *")
    print("***********")
    print(text)
    print([(topic+1, prob) for (topic, prob) in model[dictionary.doc2bow(doc)] if prob > 0.1])
    print()

***********
* doc 1   *
***********
Londres, Berlin, Rome et Bruxelles correspondants - Jeudi 26 mars, les Vingt-Sept devaient se réunir en visioconférence pour la troisième fois en moins de trois semaines. Au programme des discussions, la crise due au coronavirus, alors que l'Europe entière à l'exception de la Suède est confinée, que des centaines de malades meurent tous les jours et que l'économie continentale est en voie de paralysie.   Si l'urgence est bien sà»r sanitaire, ils se retrouvent alors que les tabous économiques européens tombent les uns après les autres. En quelques semaines, le pacte de stabilité et de croissance, qui régit la sacro-sainte discipline budgétaire des pays de la zone euro, a été suspendu; l'Allemagne a présenté le plus gros budget de relance de son histoire et renoncé à l'équilibre budgétaire pourtant inscrit dans le marbre; la Commission européenne a mis des dizaines de milliards sur la table; la Banque centrale européenne (BCE) a annoncé l'injection de 

# Boucle par journaux X années

In [3]:
%%time
nlp = spacy.load("fr_core_news_sm")

for year in range(2015, 2021):
    for journal in df.CJournal.unique().tolist():

        textes = df.loc[(df.Date.str.contains(str(year), regex=True)) & (df.CJournal==journal), "Texte"]
        print(f"{journal} {year} : {len(textes)} articles")
        try :
            spacy_docs = list(nlp.pipe(textes))

            docs = []
            for doc in spacy_docs:
                tokens = []
                for token in doc:
                    if len(token.orth_) > 3 and not token.is_stop: # prétraitements 1 et 2
                        tokens.append( token.lemma_.lower() )  # TODO: prétraitements 3 et 4
                docs.append( tokens )

            bigram = Phrases(docs, min_count=10)

            for index in range(len(docs)):
                for token in bigram[docs[index]]:
                    if '_' in token:  # les bigrammes peuvent être reconnus par "_" qui concatène les mots
                        docs[index].append(token) # TODO

            dictionary = Dictionary()

            # Ajouter les documents un par un au dictionnaire
            for doc in docs:
                dictionary.add_documents([doc])

            corpus = [ dictionary.doc2bow(doc) for doc in docs] # TODO
            model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=10, chunksize=1000, passes=5, random_state=1) # A REMPLIR

            for (topic, words) in model.print_topics():
                print("***********")
                print("* topic", topic+1, "*")
                print("***********")
                print(topic+1, ":", words)
                print()

            pyLDAvis.enable_notebook()
            warnings.filterwarnings("ignore", category=DeprecationWarning) 

            display(pyLDAvis.gensim_models.prepare(model, corpus, dictionary, sort_topics=False))
        except:
            print("error")

Figaro 2015 : 775 articles
***********
* topic 1 *
***********
1 : 0.009*"parti" + 0.007*"droite" + 0.006*"gauche" + 0.005*"merkel" + 0.004*"réfugié" + 0.004*"dernier" + 0.004*"angela" + 0.004*"politique" + 0.004*"européen" + 0.004*"ministre"

***********
* topic 2 *
***********
2 : 0.006*"droite" + 0.006*"politique" + 0.004*"pays" + 0.004*"france" + 0.004*"migrant" + 0.004*"européen" + 0.003*"national" + 0.003*"frontière" + 0.003*"gauche" + 0.003*"parti"

***********
* topic 3 *
***********
3 : 0.005*"pays" + 0.004*"réfugié" + 0.004*"russe" + 0.003*"immigration" + 0.003*"allemagne" + 0.003*"migrant" + 0.003*"syrien" + 0.003*"faire" + 0.003*"bien" + 0.003*"année"

***********
* topic 4 *
***********
4 : 0.007*"européen" + 0.006*"politique" + 0.005*"france" + 0.005*"faire" + 0.004*"français" + 0.004*"europe" + 0.004*"gauche" + 0.004*"ministre" + 0.004*"pays" + 0.004*"euro"

***********
* topic 5 *
***********
5 : 0.020*"européen" + 0.011*"pays" + 0.011*"frontière" + 0.011*"europe" + 0.0

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.021769  0.099932       1        1   6.131817
1      0.019080  0.053826       2        1   3.874855
2      0.051154 -0.018975       3        1   1.833759
3      0.004248  0.051248       4        1  14.193424
4     -0.108986 -0.046333       5        1   9.902014
5     -0.033877  0.038334       6        1   5.204583
6     -0.053223 -0.050870       7        1  14.998233
7      0.111195 -0.077438       8        1   3.444681
8     -0.050709 -0.018426       9        1  30.846733
9      0.039350 -0.031298      10        1   9.569900, topic_info=           Term         Freq        Total Category  logprob  loglift
237     migrant  1248.000000  1248.000000  Default  30.0000  30.0000
148    européen  1600.000000  1600.000000  Default  29.0000  29.0000
1562  frontière   819.000000   819.000000  Default  28.0000  28.0000
1104     droite   354.000000   354.000000  Default  27.0000  27.0000
1749      parti   375.000000   375.000000  Default  26.0000  26.0000
...         ...          ...          ...      ...      ...      ...
424        bien    47.812678   459.514068  Topic10  -6.0147   0.0837
176       grand    46.001074   392.108016  Topic10  -6.0533   0.2037
211        jour    46.012855   414.744619  Topic10  -6.0530   0.1478
109     dernier    45.747535   532.548330  Topic10  -6.0588  -0.1080
23        année    45.362475   527.946874  Topic10  -6.0673  -0.1078

[872 rows x 6 columns], token_table=       Topic      Freq      Term
term                            
11043      9  0.828119      "mer
12766      3  0.485374    21.000
7840       7  0.816605     5.000
13643      6  0.820224   710.000
6817       4  0.764011    75.000
...      ...       ...       ...
408       10  0.203483  étranger
7405       1  0.150275    évêque
7405       4  0.075137    évêque
7405       7  0.075137    évêque
7405       8  0.525961    évêque

[2728 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

Monde 2015 : 538 articles
***********
* topic 1 *
***********
1 : 0.008*"pays" + 0.007*"réfugié" + 0.005*"europe" + 0.005*"france" + 0.005*"européen" + 0.004*"syrie" + 0.004*"politique" + 0.004*"contre" + 0.004*"syrien" + 0.004*"allemagne"

***********
* topic 2 *
***********
2 : 0.010*"réfugié" + 0.010*"européen" + 0.009*"pays" + 0.009*"migrant" + 0.006*"europe" + 0.006*"asile" + 0.006*"ministre" + 0.005*"frontière" + 0.005*"etat" + 0.004*"personne"

***********
* topic 3 *
***********
3 : 0.007*"politique" + 0.006*"parti" + 0.006*"pays" + 0.005*"ministre" + 0.005*"gouvernement" + 0.005*"réfugié" + 0.005*"européen" + 0.004*"polonais" + 0.004*"europe" + 0.004*"droite"

***********
* topic 4 *
***********
4 : 0.010*"allemand" + 0.006*"réfugié" + 0.006*"allemagne" + 0.006*"pays" + 0.004*"merkel" + 0.004*"politique" + 0.004*"européen" + 0.003*"parti" + 0.003*"droite" + 0.003*"ministre"

***********
* topic 5 *
***********
5 : 0.005*"région" + 0.004*"faire" + 0.004*"droite" + 0.004*"politi

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


...

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.112560  0.139698       1        1  28.640639
1      0.048007 -0.010498       2        1   4.761938
2      0.006023 -0.006453       3        1   0.037332
3     -0.161922  0.041967       4        1  24.855685
4     -0.005173  0.000129       5        1   0.037332
5     -0.016248  0.000291       6        1   0.037332
6     -0.118067 -0.011578       7        1   9.180256
7      0.066158 -0.150516       8        1  16.159053
8      0.074765  0.002367       9        1  16.253100
9     -0.006102 -0.005406      10        1   0.037332, topic_info=         Term       Freq      Total Category  logprob  loglift
351     paris  29.000000  29.000000  Default  30.0000  30.0000
578      grec  26.000000  26.000000  Default  29.0000  29.0000
338     maire  26.000000  26.000000  Default  28.0000  28.0000
134   migrant  45.000000  45.000000  Default  27.0000  27.0000
314   hidalgo  16.000000  16.000000  Default  26.0000  26.0000
..        ...        ...        ...      ...      ...      ...
77     europe   0.001381  26.141675  Topic10  -7.3683  -1.9554
151    passer   0.001318  17.954127  Topic10  -7.4151  -1.6265
118      jour   0.001307  17.752332  Topic10  -7.4230  -1.6231
352  parisien   0.001306  18.013460  Topic10  -7.4238  -1.6385
314   hidalgo   0.001293  16.879296  Topic10  -7.4342  -1.5839

[739 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
991       1  0.123221            
991       4  0.123221            
991       7  0.123221            
991       8  0.246441            
991       9  0.369662            
...     ...       ...         ...
1575      8  0.926481        état
222       2  1.011283        étau
2054      9  0.735631  évacuation
2090      9  0.844580      évacué
2091      9  0.848404  évidemment

[810 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

Echos 2020 : 3 articles
***********
* topic 1 *
***********
1 : 0.002*"etat" + 0.002*"conseil_etat" + 0.002*"sauvé" + 0.001*"conseil" + 0.001*"jean-marc_sauvé" + 0.001*"jean-marc" + 0.001*"donnée" + 0.001*"ancien" + 0.001*"homme" + 0.001*"ministre"

***********
* topic 2 *
***********
2 : 0.005*"etat" + 0.005*"conseil" + 0.004*"conseil_etat" + 0.004*"jean-marc_sauvé" + 0.003*"ancien" + 0.003*"sauvé" + 0.003*"général" + 0.003*"homme" + 0.003*"ministre" + 0.002*"droit"

***********
* topic 3 *
***********
3 : 0.003*"conseil" + 0.003*"etat" + 0.002*"donnée" + 0.002*"conseil_etat" + 0.002*"faire" + 0.002*"jean-marc" + 0.002*"jean-marc_sauvé" + 0.002*"ancien" + 0.002*"politique" + 0.002*"grand"

***********
* topic 4 *
***********
4 : 0.004*"donnée" + 0.002*"grand" + 0.002*"social" + 0.002*"problème" + 0.002*"organisme" + 0.002*"conseil" + 0.002*"faire" + 0.002*"science" + 0.002*"data.org" + 0.002*"développement"

***********
* topic 5 *
***********
5 : 0.004*"etat" + 0.004*"conseil" + 0.00

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.005365  0.003046       1        1   0.016148
1     -0.028850  0.016679       2        1   0.016148
2     -0.004640  0.000442       3        1   0.016148
3      0.014637  0.011793       4        1   0.016148
4     -0.016614  0.007740       5        1   0.016148
5     -0.154736  0.092269       6        1  58.322558
6     -0.002870  0.001760       7        1   0.016148
7      0.213857  0.060753       8        1  25.474726
8     -0.006443 -0.000105       9        1   0.016148
9     -0.008977 -0.194376      10        1  16.089678, topic_info=                Term       Freq      Total Category  logprob  loglift
367          conseil  17.000000  17.000000  Default  30.0000  30.0000
85              etat  19.000000  19.000000  Default  29.0000  29.0000
368     conseil_etat  12.000000  12.000000  Default  28.0000  28.0000
923           donnée  17.000000  17.000000  Default  27.0000  27.0000
544  jean-marc_sauvé  10.000000  10.000000  Default  26.0000  26.0000
..               ...        ...        ...      ...      ...      ...
49         confiance   1.495037   2.625191  Topic10  -5.2960   1.2640
32               bon   1.494686   2.615717  Topic10  -5.2962   1.2674
98              fort   1.492108   3.507361  Topic10  -5.2979   0.9723
152             pays   1.490939   2.510761  Topic10  -5.2987   1.3058
84         essentiel   1.490473   2.614849  Topic10  -5.2990   1.2649

[703 rows x 6 columns], token_table=      Topic      Freq        Term
term                             
0        10  0.590027       -elle
235       6  0.866176        2010
2        10  1.021142  absolument
242       6  1.021557        abus
864       8  0.937992      accord
...     ...       ...         ...
845       6  0.876406    élection
221      10  1.022214     élément
222      10  1.024357     émettre
850       6  0.966393     épisode
856       6  0.866535    étranger

[425 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

Wall time: 32min 30s


Brouillon

In [48]:
%%time
nlp = spacy.load("fr_core_news_sm")
for year in range(2009, 2021):
    for journal in df.CJournal.unique().tolist():
        data = df.loc[(df['Date'].str.contains(str(year), regex=True))&(df['CJournal']==journal), ["Titre"]]
        
        textes = data["Titre"]

        try :
            spacy_docs = list(nlp.pipe(textes))
            print(spacy_docs)

            docs = []
            for doc in spacy_docs:
                tokens = []
                for token in doc:
                    if len(token.orth_) > 3 and not token.is_stop: # prétraitements 1 et 2
                        tokens.append( token.lemma_.lower() )  # TODO: prétraitements 3 et 4
                docs.append( tokens )

            bigram = Phrases(docs, min_count=10)

            for index in range(len(docs)):
                for token in bigram[docs[index]]:
                    if '_' in token:  # les bigrammes peuvent être reconnus par "_" qui concatène les mots
                        docs[index].append(token) # TODO

            dictionary = Dictionary()

            # Ajouter les documents un par un au dictionnaire
            for doc in docs:
                dictionary.add_documents([doc])

            corpus = [ dictionary.doc2bow(doc) for doc in docs]
            model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=10, chunksize=1000, passes=5, random_state=1) # A REMPLIR

            print(year, journal, len(data), " articles")
            pyLDAvis.enable_notebook()
            warnings.filterwarnings("ignore", category=DeprecationWarning) 

            display(pyLDAvis.gensim_models.prepare(model, corpus, dictionary, sort_topics=False))
        except :
            continue
        break

[]
[La "jungle" de Calais évacuée devant les caméras   Eric Besson a voulu envoyer « un signal fort » à ses collègues de l'UMP]
2009 Monde 1  articles


C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=         x    y  topics  cluster       Freq
topic                                      
0      0.0 -0.0       1        1   0.833335
1      0.0 -0.0       2        1   0.833335
2     -0.0  0.0       3        1   0.833335
3     -0.0 -0.0       4        1   0.833335
4     -0.0 -0.0       5        1  92.499983
5     -0.0 -0.0       6        1   0.833335
6     -0.0  0.0       7        1   0.833335
7      0.0  0.0       8        1   0.833335
8      0.0  0.0       9        1   0.833335
9     -0.0  0.0      10        1   0.833335, topic_info=        Term      Freq  Total Category  logprob  loglift
1      calai  1.000000    1.0  Default  11.0000     11.0
7     jungle  1.000000    1.0  Default  10.0000     10.0
6       fort  0.000000    0.0  Default   9.0000      9.0
3   collègue  0.000000    0.0  Default   8.0000      8.0
0     besson  0.000000    0.0  Default   7.0000      7.0
..       ...       ...    ...      ...      ...      ...
1      calai  0.008333    1.0  Topic10  -2.3979     -0.0
0     besson  0.008333    1.0  Topic10  -2.3979     -0.0
6       fort  0.008333    1.0  Topic10  -2.3979     -0.0
3   collègue  0.008333    1.0  Topic10  -2.3979     -0.0
7     jungle  0.008333    1.0  Topic10  -2.3979     -0.0

[121 rows x 6 columns], token_table=      Topic  Freq      Term
term                       
0         5   1.0    besson
1         5   1.0     calai
2         5   1.0    caméra
3         5   1.0  collègue
4         5   1.0   envoyer
5         5   1.0      eric
6         5   1.0      fort
7         5   1.0    jungle
8         5   1.0    signal
9         5   1.0   vouloir
10        5   1.0   évacuer, R=11, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

[]
[Athènes demande de l'aide à l'UE pour faire face à une  crise migratoire]
2010 Monde 1  articles


C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


...

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.057800 -0.133958       1        1  12.169508
1      0.140308 -0.000229       2        1  11.811827
2      0.024275  0.090825       3        1  13.424848
3     -0.057559  0.004182       4        1   9.000998
4     -0.007741 -0.045585       5        1   9.033449
5     -0.095689 -0.079285       6        1  11.390228
6     -0.051163  0.075313       7        1   8.177901
7      0.035686  0.056688       8        1   9.591926
8      0.037198  0.019660       9        1   6.282963
9     -0.083115  0.012389      10        1   9.116352, topic_info=        Term       Freq      Total Category  logprob  loglift
249   figaro   9.000000   9.000000  Default  30.0000  30.0000
252  premium   7.000000   7.000000  Default  29.0000  29.0000
250   lettre   7.000000   7.000000  Default  28.0000  28.0000
247     2019   6.000000   6.000000  Default  27.0000  27.0000
177    crise  13.000000  13.000000  Default  26.0000  26.0000
..       ...        ...        ...      ...      ...      ...
83     trump   0.675571   8.790978  Topic10  -5.6468  -0.1708
323   avenir   0.669208   3.182669  Topic10  -5.6563   0.8357
188     rome   0.669207   3.199230  Topic10  -5.6563   0.8305
801     vote   0.669205   2.485759  Topic10  -5.6563   1.0829
100     bien   0.669205   1.902207  Topic10  -5.6563   1.3504

[550 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
38        4  0.806775      1897
488       2  0.252034      2015
488       3  0.504069      2015
488       8  0.252034      2015
590       1  0.223517      2018
...     ...       ...       ...
726       9  0.861614       élu
452       1  0.772887   étrange
12        2  0.378066  étranger
12        3  0.378066  étranger
12        5  0.189033  étranger

[725 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

[L'agenda caché de Moscou en Italie, Élargissement de lâUnion européenne à lâheure du Coronavirus: «une fuite en avant suicidaire dans le déni», Coronavirus, un révélateur des faiblesses de la construction européenne?, EN BREF, Coralie Delaume: «Un choc externe pourrait provoquer lâéclatement de lâUnion européenne», Syrie: le président turc demande le «soutien concret» de l'Otan, L'euphémisme de la « crise migratoire », «Vague migratoire: le seul moyen de faire reculer Erdogan, câest de lui tenir tête», La Lettre du Figaro du 6 mars 2020, Frans Timmermans : « Ce projet de loi est révolutionnaire », Il faut défendre les frontières de l'Europe !, Macron vise l'entente à Varsovie  Le président français arrive en Pologne dans le but de se réconcilier avec ce pays et l'Europe centrale., Turquie : comment les passeurs utilisent Instagram pour recruter les migrants  Alors que les départs reprennent vers l'Europe, la publicité de cette industrie n'est plus souterraine., Municipales à Pari

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0      0.036189 -0.006362       1        1   7.467730
1      0.065355 -0.050333       2        1   9.316496
2     -0.129837  0.074740       3        1  13.611688
3      0.028934  0.070237       4        1   5.208447
4      0.013784  0.001205       5        1   3.889763
5      0.012420 -0.032711       6        1   9.286788
6     -0.053416 -0.025012       7        1  10.837340
7      0.089479  0.116483       8        1  11.625194
8     -0.112930 -0.044417       9        1  14.577029
9      0.050020 -0.103830      10        1  14.179526, topic_info=           Term      Freq     Total Category  logprob  loglift
33      erdogan  5.000000  5.000000  Default  30.0000  30.0000
29        crise  2.000000  2.000000  Default  29.0000  29.0000
31   migratoire  3.000000  3.000000  Default  28.0000  28.0000
6      européen  3.000000  3.000000  Default  27.0000  27.0000
50    frontière  5.000000  5.000000  Default  26.0000  26.0000
..          ...       ...       ...      ...      ...      ...
102      angela  0.724923  1.836325  Topic10  -4.3345   1.0239
101   allemagne  0.725075  1.855070  Topic10  -4.3343   1.0140
6      européen  0.725526  3.792250  Topic10  -4.3336   0.2996
50    frontière  0.725502  5.930380  Topic10  -4.3337  -0.1476
33      erdogan  0.725024  5.838643  Topic10  -4.3343  -0.1327

[406 rows x 6 columns], token_table=      Topic      Freq           Term
term                                
117       7  0.864496           1500
39        3  0.544386           2020
39        9  0.544386           2020
255       3  0.836465          abeba
94        6  0.567246         accord
...     ...       ...            ...
60        9  0.832979          viser
80        8  0.849785       échapper
213       8  0.849785           égée
11        6  0.891682  élargissement
235       8  0.849785       étranger

[303 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

Wall time: 1min 7s


In [21]:
# Ouvertur d'une fenêtre pour télécharger tous les packages et avoir les stopswords français
# nltk.download()

stopwords_fr_ntlk = set(nltk.corpus.stopwords.words('french'))

In [63]:
import json
import spacy
import pandas as pd
from gensim.corpora.dictionary import Dictionary
from gensim.models import Phrases, LdaModel
import pyLDAvis.gensim_models
import warnings

# Assurez-vous d'avoir installé et importé toutes les bibliothèques nécessaires

# Assurez-vous d'avoir défini votre DataFrame 'df'

nlp = spacy.load("fr_core_news_sm")
dictionary = Dictionary()

for year in range(2009, 2021):
    for journal in df.CJournal.unique().tolist():
        data = df.loc[(df['Date'].str.contains(str(year), regex=True))&(df['CJournal']==journal), ["Texte"]]
        
        textes = data[["Texte"]].iloc[:100]

        try:
            spacy_docs = list(nlp.pipe(textes))

            docs = []
            for doc in spacy_docs:
                tokens = []
                for token in doc:
                    if len(token.orth_) > 3 and not token.is_stop: 
                        tokens.append(token.lemma_.lower())
                docs.append(tokens)

            bigram = Phrases(docs, min_count=10)

            for index in range(len(docs)):
                for token in bigram[docs[index]]:
                    if '_' in token:  
                        docs[index].append(token)

            # Ajouter les documents au dictionnaire
            for doc in docs:
                dictionary.add_documents([doc])

            # Création du corpus
            corpus = [dictionary.doc2bow(doc) for doc in docs]

            # Création du modèle LDA
            model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=10, chunksize=1000, passes=5, random_state=1)

            # Préparation des données pour PyLDAvis
            prepared_data = pyLDAvis.gensim_models.prepare(model, corpus, dictionary, sort_topics=False)

            # Sauvegarde des données du DataFrame dans un dictionnaire
            data_dict = df.to_dict()

            # Sauvegarde des données dans un fichier JSON
            with open("data.json", "w") as f:
                json.dump(data_dict, f)

            # Affichage de PyLDAvis depuis les données sauvegardées
            pyLDAvis.enable_notebook()
            warnings.filterwarnings("ignore", category=DeprecationWarning)
            pyLDAvis.display(prepared_data)

        except Exception as e:
            print(f"Erreur lors du traitement : {e}")
            continue


C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_

C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(
C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_

In [64]:
prepared_data

PreparedData(topic_coordinates=         x    y  topics  cluster       Freq
topic                                      
0      0.0  0.0       1        1   5.002285
1      0.0  0.0       2        1   5.002285
2      0.0  0.0       3        1   5.002285
3      0.0  0.0       4        1   5.002285
4      0.0  0.0       5        1   5.002285
5      0.0  0.0       6        1   5.002285
6      0.0  0.0       7        1   5.002478
7      0.0  0.0       8        1   5.002285
8      0.0  0.0       9        1   5.002285
9      0.0  0.0      10        1  54.979240, topic_info=    Term      Freq  Total Category  logprob  loglift
0  texte  1.000000    1.0  Default      1.0      1.0
0  texte  0.050023    1.0   Topic1      0.0      0.0
0  texte  0.050023    1.0   Topic2      0.0      0.0
0  texte  0.050023    1.0   Topic3      0.0      0.0
0  texte  0.050023    1.0   Topic4      0.0      0.0
0  texte  0.050023    1.0   Topic5      0.0      0.0
0  texte  0.050023    1.0   Topic6      0.0      0.0
0  texte  0.050025    1.0   Topic7      0.0      0.0
0  texte  0.050023    1.0   Topic8      0.0      0.0
0  texte  0.050023    1.0   Topic9      0.0      0.0
0  texte  0.549792    1.0  Topic10      0.0      0.0, token_table=      Topic  Freq   Term
term                    
0        10   1.0  texte, R=1, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

In [38]:
import string

# Fonction de prétraitement améliorée
def preprocess_text(text):
    french_stopwords = set(nltk.corpus.stopwords.words('french'))
    # Suppression de la ponctuation
    text = text.translate(str.maketrans('', '', string.punctuation))
    # Tokenization et suppression des mots vides
    tokens = [token for token in word_tokenize(text, language="french") if token.lower() not in french_stopwords]
    return tokens

textes = df["Texte"].iloc[:10]
# print(f"Texte initial \n{textes}")

# Prétraitement du texte
preprocessed_texts = [preprocess_text(text) for text in textes]

# print(f"\nTextes prétraités :\n{preprocessed_texts}")

dictionary = Dictionary(preprocessed_texts)

# Création du corpus
corpus = [dictionary.doc2bow(text) for text in preprocessed_texts]

# Création du modèle LDA
model = LdaModel(corpus=corpus, id2word=dictionary, num_topics=10, chunksize=1000, passes=5, random_state=1)

# Affichage des résultats
pyLDAvis.enable_notebook()
warnings.filterwarnings("ignore", category=DeprecationWarning)
display(pyLDAvis.gensim_models.prepare(model, corpus, dictionary, sort_topics=False))


C:\Users\tlp\Anaconda3\lib\site-packages\pyLDAvis\_prepare.py:243: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  default_term_info = default_term_info.sort_values(


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
0     -0.090863 -0.020479       1        1   8.400920
1      0.008801 -0.004391       2        1   0.015277
2      0.001485 -0.000403       3        1   0.015277
3      0.011510  0.014310       4        1   4.957939
4     -0.065620 -0.015605       5        1  13.026790
5      0.056753  0.152394       6        1  54.930442
6     -0.070054 -0.028334       7        1   8.048970
7      0.132725 -0.103175       8        1  10.573830
8      0.008442  0.006945       9        1   0.015277
9      0.006821 -0.001262      10        1   0.015277, topic_info=            Term       Freq      Total Category  logprob  loglift
38             a  91.000000  91.000000  Default  30.0000  30.0000
276            »  89.000000  89.000000  Default  29.0000  29.0000
275            «  82.000000  82.000000  Default  28.0000  28.0000
195         plus  50.000000  50.000000  Default  27.0000  27.0000
75         crise  34.000000  34.000000  Default  26.0000  26.0000
..           ...        ...        ...      ...      ...      ...
123         fait   0.000505  12.660433  Topic10  -7.5901  -1.3437
898           si   0.000503  13.582236  Topic10  -7.5930  -1.4169
74   coronavirus   0.000510  17.036308  Topic10  -7.5791  -1.6296
996         zone   0.000499  12.144493  Topic10  -7.6022  -1.3141
615   frontières   0.000499  19.034035  Topic10  -7.6014  -1.7627

[704 rows x 6 columns], token_table=      Topic      Freq         Term
term                              
0         6  0.988296            1
2481      7  0.569392     20072008
293       6  0.987610         2012
2693      4  1.063813     20152016
2066      1  0.335745           27
...     ...       ...          ...
1695      8  0.552719      émotion
2805      4  1.016941         état
1255      5  0.749457  étrangement
1009      6  0.816738         être
1009      8  0.116677         être

[700 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[1, 2, 3, 4, 5, 6, 7, 8, 9, 10])